In [1]:
from tqdm import tqdm
import shutil
import json
import glob
import random
from pathlib import Path
import subprocess
import os

import pandas as pd
from warnings import simplefilter
simplefilter(action="ignore", category=pd.errors.PerformanceWarning)
import numpy as np

creating dirs for classifyng extracted features by 3 classes

In [27]:
parent_dir = '/Users/anastasiiapovolotskaia/Desktop/cough'

# extracted features by classes
features_dir = {'audio_sets': ['healthy', 'unhealthy', 'train', 'validation', 'test']}
# extracted features sorted by sets
# tr_val_test = {'audio_sets': ['train', 'validation', 'test']}

def make_dir(parent_dir, dirs):
    for key, values in dirs.items():
        path = os.path.join(parent_dir, key)
        if os.path.exists(path):
            print("Directory '% s' already exists" % key)
        else:
            os.mkdir(path)
            print("Directory '% s' created" % key)
            print(f'Path of {key} dir:', path)
        for v in values:
            path = os.path.join(parent_dir, key, v)
            if os.path.exists(path):
                print("Directory '% s' already exists" % v)
            else:
                os.mkdir(path)
                print("Directory '% s' created" % v)
                print(f'Path of {v} dir:', path)

make_dir(parent_dir, features_dir)
# make_dir(parent_dir, tr_val_test)

Directory 'audio_sets' created
Path of audio_sets dir: /Users/anastasiiapovolotskaia/Desktop/cough/audio_sets
Directory 'healthy' created
Path of healthy dir: /Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/healthy
Directory 'unhealthy' created
Path of unhealthy dir: /Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/unhealthy
Directory 'train' created
Path of train dir: /Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/train
Directory 'validation' created
Path of validation dir: /Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/validation
Directory 'test' created
Path of test dir: /Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/test


In [28]:
healthy_path = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/healthy'
unhealthy_path = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/unhealthy'

In [29]:
dir = glob.glob('/Users/anastasiiapovolotskaia/Desktop/cough/public_dataset/*.json')

## Counting audio files in two splits: healthy and unhealthy

function for opensmile feature extractor

In [30]:
healthy = 0
unhealthy = 0

for file in tqdm(dir):
    with open(file) as f:
        data = json.load(f)
        if'status' in data:
            file_name = file.split('.')[0] # geting path and name of a file without .json extension
            wav_file = file_name + '.wav' # get wav analogue
            if data['status'] == 'healthy':
                new_file = wav_file.split('/')[-1].split('.')[0] + '_0' + '.wav'
                new_name = os.path.join(healthy_path, new_file)
                shutil.copy(wav_file, new_name)
                healthy += 1
            elif data['status'] == 'COVID-19' or data['status'] == 'symptomatic':
                new_file = wav_file.split('/')[-1].split('.')[0] + '_1' + '.wav'
                new_name = os.path.join(unhealthy_path, new_file)
                shutil.copy(wav_file, new_name)

                unhealthy += 1

print()
print('Healthy cough:', healthy)
print('Unhealthy cough:', unhealthy)

100%|██████████| 27550/27550 [00:28<00:00, 965.29it/s] 


Healthy cough: 12479
Unhealthy cough: 3745


## Stating how many files should be in each set

unhealthy cough files

In [31]:
train_size_unhealthy = int(unhealthy * 0.70)
val_size_unhealthy = int(unhealthy * 0.15)
test_size_unhealthy = int(unhealthy * 0.15)

print(train_size_unhealthy)
print(val_size_unhealthy)
print(test_size_unhealthy)

2621
561
561


healthy cough files

In [32]:
train_size_healthy = 2621 # meanwhile total 12479
val_size_healthy = 561 # 1872
test_size_healthy = 561 # 1872

print(train_size_healthy)
print(val_size_healthy)
print(test_size_healthy)

2621
561
561


In [33]:
total_train = train_size_healthy + train_size_unhealthy
total_val = val_size_healthy + val_size_unhealthy
total_test = test_size_healthy +test_size_unhealthy

total = total_train + total_val + total_test
total

7486

## Sorting into three sets

In [9]:
audio_train = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/train'
audio_val = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/validation'
audio_test = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/test'

In [10]:
def sorting_files(i, wav_file,
                  train_size=train_size_healthy, val_size=val_size_healthy, test_size=test_size_healthy,
                  train_dir=audio_train, val_dir=audio_val, test_dir=audio_test):
    if i < train_size:
        shutil.copy(wav_file, train_dir)
    elif i < (train_size + val_size):
        shutil.copy(wav_file, val_dir)
    elif i < (train_size + val_size + test_size):
        shutil.copy(wav_file, test_dir)

In [11]:
def form_three_sets(dir):
    for i, file in enumerate(tqdm(glob.glob(dir))):
        sorting_files(i, file)
    return 'Sorting is over'

In [13]:
form_three_sets('/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/healthy/*.wav')

  0%|          | 0/12479 [00:00<?, ?it/s]

100%|██████████| 12479/12479 [00:01<00:00, 12033.58it/s]


'Sorting is over'

In [14]:
form_three_sets('/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/unhealthy/*.wav')

100%|██████████| 1155/1155 [00:01<00:00, 1106.04it/s]


'Sorting is over'

## Extracting features

In [16]:
def feature_extractor(wav_file, save_path):
    smilextract = '/Users/anastasiiapovolotskaia/Desktop/opensmile-master/build/progsrc/smilextract/SMILExtract'
    config = '/Users/anastasiiapovolotskaia/Desktop/opensmile-master/config/gemaps/v01b/GeMAPSv01b.conf'

    opensmile_cmd = [smilextract, '-C', config, '-I', wav_file, '-csvoutput', save_path]
    execution_result = subprocess.check_call(opensmile_cmd)

In [18]:
def extract_features(path, save_path_features, save_path_labels):

    labels = []

    for file in tqdm(glob.glob(path)):
        cls = file.split('/')[-1].split('.')[0].split('_')[-1]
        labels.append(int(cls))
        feature_extractor(file, save_path_features)


    df_labels = pd.DataFrame(labels)
    df_labels.to_csv(save_path_labels, header=False, index=False)

    return 'Features extraction is over'

In [19]:
save_path_train_features = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/train_gemaps.csv'
save_path_val_features = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/val_gemaps.csv'
save_path_test_features = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/test_gemaps.csv'

In [21]:
save_path_train_labels = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/train_gemaps_targets.csv'
save_path_val_labels = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/val_gemaps_targets.csv'
save_path_test_labels = '/Users/anastasiiapovolotskaia/Desktop/cough/audio_sets/test_gemaps_targets.csv'


In [22]:
extract_features(audio_train+'/*.wav', save_path_train_features, save_path_train_labels)

  0%|          | 0/1616 [00:00<?, ?it/s](MSG) [2] SMILExtract: openSMILE starting!
(MSG) [2] SMILExtract: config file is: /Users/anastasiiapovolotskaia/Desktop/opensmile-master/config/gemaps/v01b/GeMAPSv01b.conf
(MSG) [2] cComponentManager: successfully registered 102 component types.
(MSG) [2] instance 'gemapsv01b_logSpectral': logSpecFloor = -140.00  (specFloor = 1.000000e-14)
(MSG) [2] instance 'lldsink': No filename given, disabling this sink component.
(MSG) [2] instance 'lldhtksink': No filename given, disabling this sink component.
(MSG) [2] instance 'lldarffsink': No filename given, disabling this sink component.
(MSG) [2] instance 'arffsink': No filename given, disabling this sink component.
(MSG) [2] instance 'htksink': No filename given, disabling this sink component.
(MSG) [2] cComponentManager: successfully finished createInstances (55 component instances were finalised, 1 data memories were finalised)
(MSG) [2] cComponentManager: starting single thread processing loop
(WR

'Features extraction is over'

In [23]:
extract_features(audio_val+'/*.wav', save_path_val_features, save_path_val_labels)

  0%|          | 0/346 [00:00<?, ?it/s](MSG) [2] SMILExtract: openSMILE starting!
(MSG) [2] SMILExtract: config file is: /Users/anastasiiapovolotskaia/Desktop/opensmile-master/config/gemaps/v01b/GeMAPSv01b.conf
(MSG) [2] cComponentManager: successfully registered 102 component types.
(MSG) [2] instance 'gemapsv01b_logSpectral': logSpecFloor = -140.00  (specFloor = 1.000000e-14)
(MSG) [2] instance 'lldsink': No filename given, disabling this sink component.
(MSG) [2] instance 'lldhtksink': No filename given, disabling this sink component.
(MSG) [2] instance 'lldarffsink': No filename given, disabling this sink component.
(MSG) [2] instance 'arffsink': No filename given, disabling this sink component.
(MSG) [2] instance 'htksink': No filename given, disabling this sink component.
(MSG) [2] cComponentManager: successfully finished createInstances (55 component instances were finalised, 1 data memories were finalised)
(MSG) [2] cComponentManager: starting single thread processing loop
(WRN

'Features extraction is over'

In [24]:
extract_features(audio_test+'/*.wav', save_path_test_features, save_path_test_labels)

  0%|          | 0/346 [00:00<?, ?it/s](MSG) [2] SMILExtract: openSMILE starting!
(MSG) [2] SMILExtract: config file is: /Users/anastasiiapovolotskaia/Desktop/opensmile-master/config/gemaps/v01b/GeMAPSv01b.conf
(MSG) [2] cComponentManager: successfully registered 102 component types.
(MSG) [2] instance 'gemapsv01b_logSpectral': logSpecFloor = -140.00  (specFloor = 1.000000e-14)
(MSG) [2] instance 'lldsink': No filename given, disabling this sink component.
(MSG) [2] instance 'lldhtksink': No filename given, disabling this sink component.
(MSG) [2] instance 'lldarffsink': No filename given, disabling this sink component.
(MSG) [2] instance 'arffsink': No filename given, disabling this sink component.
(MSG) [2] instance 'htksink': No filename given, disabling this sink component.
(MSG) [2] cComponentManager: successfully finished createInstances (55 component instances were finalised, 1 data memories were finalised)
(MSG) [2] cComponentManager: starting single thread processing loop
(WRN

'Features extraction is over'